In [1]:
import time
import statistics as stats
import multiprocessing
import time 
import random
import time
from tqdm import tqdm
from datetime import timedelta
from datetime import datetime
start_program = time.time()
from multiprocessing import *
import pandas as pd
import numpy as np
from threading import Thread
import time
import subprocess 


In [2]:
results = [[] for i in range(5)]

n_it = 100


n_st = number_stations = 10
n_s = number_sensors = 100

def_st = 1
def_s = 3
def_r = 'day'


set_date = [random.random() for i in range(500)]


In [3]:

def str_time_prop(start, end, time_format, prop):
    """Get a time at a proportion of a range of two formatted times.

    start and end should be strings specifying times formatted in the
    given format (strftime-style), giving an interval [start, end].
    prop specifies how a proportion of the interval to be taken after
    start.  The returned time will be in the specified format.
    """

    stime = time.mktime(time.strptime(start, time_format))
    etime = time.mktime(time.strptime(end, time_format))

    ptime = stime + prop * (etime - stime)

    return time.strftime(time_format, time.localtime(ptime))



def random_date(start, end, prop, dform = '%Y-%m-%dT%H:%M:%S'):
    return str_time_prop(start, end, dform, prop)
    
    
def to_pm(v):
    return str(round(v[0][0],2)) + "$" + '\\' + "pm$" + str(round(v[1][0],2))


# Queries

In [4]:
iw_q1 = """
    select time, id_station, <sid> FROM "<db>"."autogen"."sensor" 
    where <stid> 
    AND time > '<timestamp>Z' - <nb><rangesUnit> 
    AND  time < '<timestamp>Z'
"""

iw_q2 = """
    select time, id_station, <sid> FROM "<db>"."autogen"."sensor" 
    where <stid> 
    AND time > '<timestamp>Z' - <nb><rangesUnit> 
    AND  time < '<timestamp>Z' 
    and <sfilter>
""" #s<sid>

iw_q3 = """
    SELECT <avg_s> FROM "<db>"."autogen"."sensor" 
    WHERE  time > '<timestamp>Z' - <nb><rangesUnit> 
    AND time < '<timestamp>Z' 
    and <stid> 
    GROUP BY "id_station"  
"""  #mean(s<sid>)

iw_q4 = """
    SELECT first(id_station), <avg_s> FROM "<db>"."autogen"."sensor" 
    WHERE time > '<timestamp>Z' - <nb><rangesUnit> 
    and time < '<timestamp>Z' 
    and <stid> 
    GROUP BY id_station,time(1h)
""" #mean(s<sid>)
iw_q5 = """
    SELECT id_station, mean_value FROM (SELECT <avg_s> as mean_value FROM "<db>"."autogen"."sensor" 
    WHERE time > '<timestamp>Z' - <nb><rangesUnit> 
    AND time < '<timestamp>Z' 
    and <stid> 
    GROUP BY id_station,time(5s) FILL(0)) 
    GROUP BY id_station
""" #mean(s<sid>)


In [28]:
from influxdb import InfluxDBClient
from tqdm import tqdm 
import time

class Influx_Wide:
 
    # A sample method 
    @staticmethod
    def query(query, db, max_d, rangesUnit, n_it, start_date = "2019-04-01T00:00:00", stop_date = "2019-04-30T00:00:00", n_st = 1, n_s = 10):
        client = InfluxDBClient(host="diufrm118", port=8086, username='abdel')
        results = [[],[]]
        
        duration = max_d
        runtimes = []
        full_time = time.time()
        for i in tqdm(range(n_it)):
            date = random_date(start_date, stop_date, set_date[(duration*i)%500], dform = '%Y-%m-%dT%H:%M:%S')
            temp = query.replace("<timestamp>", date)
            temp = temp.replace("<db>", db)
            temp = temp.replace("<nb>", str(duration))
            temp = temp.replace("<rangesUnit>", str(rangesUnit[0]))
#             temp = temp.replace("<sid>", str(set_s[(duration*i)%500]))
            
            
            
            li = ['st' + str(z) for z in random.sample(range(number_stations), n_st)]
#                     print(li)
            q = '(id_station =' + "'" + li[0] + "'"
            for j in li[1:]:
                q += ' OR '  + 'id_station =' + "'" + j + "'"
            q += ")"
            temp = temp.replace("<stid>", q)
            
            
            # sensor
            li = ['s' + str(z) for z in random.sample(range(number_sensors), n_s)]
            q = li[0]
            q_filter = "( " + li[0] + ' > 0.95'
            q_avg = 'mean(' + li[0] + ')'
            for j in li[1:]:
                q += ', ' + j
#                 q_filter += ' OR ' + j + ' > 0.95'
                q_avg += ', ' + 'mean(' + j + ')'
            temp = temp.replace("<sid>", q)
            temp = temp.replace("<sfilter>", q_filter + ")")
            temp = temp.replace("<avg_s>", q_avg)                
            
            
            start = time.time()
#             print(temp)
            result = client.query(temp)
            diff = (time.time()-start)*1000
#             print(temp, diff)
            runtimes.append(diff)
            if time.time() - full_time > 20 and i > 5: 
                break              
#         print(temp)
#             print(runtimes)
        results[0].append(stats.mean(runtimes))
#             results[1].append(percentile(runtimes,85))
        results[1].append(stats.stdev(runtimes))
        client.close()
        return results
    
    @staticmethod
    def insert_file(batch_size,rate, st, f):
#         template_sql = "INSERT INTO d1_wide_slow_ingest (time, id_station"
#         for i in range(100):
#             template_sql += ", s" + str(i)
#         template_sql += ") VALUES ('%s', '%s',"  + ','.join(100* [' %s']) + ');'
        template_sql = "sensor,id_station=st" + str(st) + " "

        client = InfluxDBClient(host='diufrm118', port=8086, username='abdel', database='d1_wide')
#         file = '/home/abdel/venv2/bin/insertion-100/short_ts' + str(st) + '.csv'
#         f = open(file, "r")
#         f = f.read()
#         f = f.splitlines()[1:]
# #         f = ["\n".join(f[i:i+rate])  for i in range(0, len(f), rate)]
#         for i in range(len(f)):
#             f[i] = f[i].split(',')            
#             temp = template_sql
#             temp += 's0=' + f[i][2]
#             cpt = 1
#             for e in f[i][3:]:
#                 temp += ",s" + str(cpt) + "=" + str(e)
#                 cpt += 1
#             temp += " " + str(10**3*int(datetime.timestamp( datetime.strptime(f[i][0], '%Y/%m/%dT%H:%M:%S'))))
#             f[i] = temp        
        
        start = time.time()
        a = 0
        print('insertion st' + str(st) + ' started')
        while not stop_insertion[st]: 
            starttime = time.time()
#             print(f[a*rate:(1+a)*rate])
            client.write_points(f[a*rate:(1+a)*rate], database='d1_wide', time_precision='ms', batch_size=rate, protocol='line')
            a += 1
            diff = 1.0 - ((time.time() - starttime))
            try: 
                time.sleep(diff)
            except: 
                print(diff)
                
    @staticmethod
    def insert_file_1station(batch_size,rate, st, f):
#         template_sql = "INSERT INTO d1_wide_slow_ingest (time, id_station"
#         for i in range(100):
#             template_sql += ", s" + str(i)
#         template_sql += ") VALUES ('%s', '%s',"  + ','.join(100* [' %s']) + ');'
        template_sql = "sensor,id_station=st" + str(st) + " "

        client = InfluxDBClient(host='diufrm118', port=8086, username='abdel', database='d1_wide')
#         file = '/home/abdel/venv2/bin/insertion-100/short_ts' + str(st) + '.csv'
#         f = open(file, "r")
#         f = f.read()
#         f = f.splitlines()[1:]
# #         f = ["\n".join(f[i:i+rate])  for i in range(0, len(f), rate)]
#         for i in range(len(f)):
#             f[i] = f[i].split(',')            
#             temp = template_sql
#             temp += 's0=' + f[i][2]
#             cpt = 1
#             for e in f[i][3:]:
#                 temp += ",s" + str(cpt) + "=" + str(e)
#                 cpt += 1
#             temp += " " + str(10**3*int(datetime.timestamp( datetime.strptime(f[i][0], '%Y/%m/%dT%H:%M:%S'))))
#             f[i] = temp        
        
        start = time.time()
        a = 0
        print('insertion st' + str(st) + ' started')
        while not stop_insertion[st]: 
            starttime = time.time()
#             print(f[a*rate:(1+a)*rate])
            client.write_points(f[a*rate:(1+a)*rate], database='d1_wide', time_precision='ms', batch_size=rate, protocol='line')
            a += 1
            diff = 1.0 - ((time.time() - starttime))
            try: 
                time.sleep(diff)
            except: 
                print(diff)
                                            
        
    @staticmethod
    def run_all(start, stop, db):
        results[0].append(to_pm(Influx_Wide.query(iw_q1, db, 1, def_r, n_it, start, stop, n_st = def_st, n_s = def_s)))
        results[1].append(to_pm(Influx_Wide.query(iw_q2, db, 1, def_r, n_it, start, stop, n_st = def_st, n_s = def_s)))
        results[2].append(to_pm(Influx_Wide.query(iw_q3, db, 1, def_r, n_it, start, stop, n_st = def_st, n_s = def_s)))
        results[3].append(to_pm(Influx_Wide.query(iw_q4, db, 1, def_r, n_it, start, stop, n_st = def_st, n_s = def_s)))
        results[4].append(to_pm(Influx_Wide.query(iw_q5, db, 1, def_r, n_it, start, stop, n_st = def_st, n_s = def_s)))
    
    
    
    

In [ ]:
Influx_Wide.run_all("2019-04-01T00:00:00", "2019-04-30T00:00:00", "d1_wide")

In [6]:
files = []
for st in tqdm(range(100)):
    template_sql = "sensor,id_station=st" + str(st) + " "
    file = '/home/abdel/venv2/bin/insertion-100/short_ts' + str(st) + '.csv'
    f = open(file, "r")
    f = f.read()
    f = f.splitlines()[1:]
#         f = ["\n".join(f[i:i+rate])  for i in range(0, len(f), rate)]
    for i in range(len(f)):
        f[i] = f[i].split(',')            
        temp = template_sql
        temp += 's0=' + f[i][2]
        cpt = 1
        for e in f[i][3:]:
            temp += ",s" + str(cpt) + "=" + str(e)
            cpt += 1
        temp += " " + str(10**3*int(datetime.timestamp( datetime.strptime(f[i][0], '%Y/%m/%dT%H:%M:%S'))))
        f[i] = temp   
    files.append(f)

100%|██████████████████████████████████████████████████████████████████| 100/100 [37:55<00:00, 22.75s/it]


In [27]:
files_1s = []

for i in range(len(files[0])):
    for j in range(10):
        files_1s.append(files[j][i])
len(files_1s)

2592000

In [ ]:
for i in range(100):
    

In [21]:
print(f[0])

sensor,id_station=st99 s0=0.086852,s1=0.256154,s2=0.353368,s3=0.264800,s4=0.340716,s5=0.888801,s6=0.098555,s7=0.990292,s8=0.006500,s9=0.197772,s10=0.056110,s11=0.711823,s12=0.113245,s13=0.203696,s14=0.749044,s15=0.637718,s16=0.197120,s17=0.396791,s18=0.868563,s19=0.503080,s20=0.403444,s21=0.050145,s22=0.434476,s23=0.649876,s24=0.001515,s25=0.970305,s26=0.473175,s27=0.563040,s28=0.310380,s29=0.273118,s30=0.551110,s31=0.308798,s32=0.783165,s33=0.950974,s34=0.926163,s35=0.802391,s36=0.226309,s37=0.432790,s38=0.114836,s39=0.347638,s40=0.432519,s41=0.838368,s42=0.638415,s43=0.944477,s44=0.735955,s45=0.419511,s46=0.152170,s47=0.333158,s48=0.566972,s49=0.028693,s50=0.491042,s51=0.604122,s52=0.764282,s53=0.577141,s54=0.267561,s55=0.432286,s56=0.157174,s57=0.851707,s58=0.213233,s59=0.095803,s60=0.982957,s61=0.841460,s62=0.533001,s63=0.090531,s64=0.386728,s65=0.363502,s66=0.281768,s67=0.431700,s68=0.852836,s69=0.398835,s70=0.760999,s71=0.160066,s72=0.475869,s73=0.028385,s74=0.111324,s75=0.948984

In [33]:
n_threads = 1
stop_insertion = [False for i in range(n_threads)]
rate = 10000

# 20K dp/s

# Launch insertion
for i in range(n_threads):  
    t1 = Thread(target = Influx_Wide.insert_file_1station, args=(100_000, rate, i, files_1s))
#     t1 = Thread(target = ClickHouse.insert_by_point, args=(rate, i))
    t1.setDaemon(True)
    t1.start()

# insert_new(200, 1)

insertion st0 started
-1.7371673583984375
-1.3749432563781738
-1.3923051357269287
-1.6915810108184814
-1.4253880977630615
-1.275080919265747
-1.8421576023101807
-1.4250750541687012
-1.2586636543273926
-1.6750130653381348
-1.6921019554138184
-1.9084205627441406
-1.325394868850708
-1.8333454132080078
-1.8004710674285889
-1.2833847999572754
-1.6772804260253906
-1.350172519683838
-1.6587953567504883
-1.308264970779419
-1.5587422847747803
-1.458331823348999
-1.6421966552734375
-1.316667079925537
-1.6004631519317627
-1.6250338554382324
-1.3170292377471924
-1.7249360084533691
-1.2755155563354492
-1.7332086563110352
-1.3838694095611572
-1.5250179767608643
-1.342928409576416
-1.6833741664886475
-1.3086659908294678
-1.6178007125854492
-1.683781385421753
-1.5415375232696533
-1.583841323852539
-1.8416306972503662
-1.4670674800872803
-1.4417223930358887
-1.5587432384490967
-1.3665568828582764
-1.6671524047851562
-1.4330763816833496


In [39]:
n_threads = 100
stop_insertion = [False for i in range(n_threads)]
rate = 100

# 20K dp/s

# Launch insertion
for i in range(n_threads):  
    t1 = Thread(target = Influx_Wide.insert_file, args=(100_000, rate, i, files[i]))
#     t1 = Thread(target = ClickHouse.insert_by_point, args=(rate, i))
    t1.setDaemon(True)
    t1.start()

# insert_new(200, 1)

insertion st0 started
insertion st1 started
insertion st2 started
insertion st3 started
insertion st4 started
insertion st5 started
insertion st6 started
insertion st7 started
insertion st8 started
insertion st9 started
insertion st10 started
insertion st11 started
insertion st12 started
insertion st13 started
insertion st14 started
insertion st15 started
insertion st16 started
insertion st17 started
insertion st18 startedinsertion st19 started

insertion st20 started
insertion st21 startedinsertion st22 started

insertion st23 started
insertion st24 started
insertion st25 started
insertion st26 started
insertion st27 started
insertion st28 started
insertion st29 started
insertion st30 startedinsertion st31 started
insertion st32 started

insertion st33 started
insertion st34 started
insertion st35 started
insertion st36 started
insertion st37 started
insertion st38 started
insertion st39 startedinsertion st40 started

insertion st41 started
insertion st42 started
insertion st43 starte

-0.16378164291381836
-0.3753039836883545
-0.15546250343322754
-0.1147010326385498-0.16386795043945312-0.1193079948425293-0.1784062385559082
-0.12686562538146973
-0.17948698997497559

-0.17118501663208008


-0.1764979362487793-0.13279151916503906-0.1875607967376709
-0.11177849769592285-0.4057185649871826
-0.1214134693145752
-0.1786191463470459-0.12293767929077148

-0.1210932731628418
-0.11800241470336914
-0.13013291358947754

-0.1598677635192871-0.15480351448059082
-0.14456439018249512

-0.13507604598999023-0.15817546844482422
-0.13667011260986328


-0.2517735958099365
-0.44201111793518066

-0.12638640403747559
-0.0276334285736084
-0.05752444267272949
-0.31519031524658203
-0.06033492088317871
-0.06595301628112793-0.25903749465942383

-0.06944060325622559
-0.09163165092468262
-0.02341485023498535
-0.0013096332550048828
-0.07668423652648926-0.052579402923583984
-0.049021005630493164

-0.31256651878356934
-0.0704641342163086
-0.07028937339782715
-0.06851840019226074
-0.0332179069519043-0.0

-0.14278268814086914
-0.2805311679840088-0.0753331184387207-0.13560986518859863

-0.07778644561767578
-0.14844274520874023
-0.11296725273132324

-0.12854456901550293
-0.04421520233154297-0.11035943031311035
-0.1082773208618164
-0.13569402694702148

-0.03942728042602539
-0.32729268074035645-0.41800475120544434
-0.16556835174560547
-0.16991972923278809
-0.10099267959594727
-0.0990903377532959-0.1797187328338623-0.39574122428894043-0.17342686653137207




-0.39435482025146484
-0.17517900466918945-0.4015357494354248

-0.02773594856262207-0.15784120559692383
-0.16294097900390625
-0.4144001007080078
-0.41295576095581055-0.4103691577911377-0.2438194751739502-0.24013996124267578-0.20439839363098145

-0.13842439651489258




-0.18375492095947266
-0.0360865592956543
-0.025273561477661133
-0.027903318405151367
-0.10322093963623047-0.06405997276306152

-0.013264894485473633
-0.0830068588256836-0.06667351722717285
-0.0760951042175293

-0.1280980110168457-0.11406135559082031
-0.12707114219665527
-0.

-0.10641717910766602
-0.10105109214782715
-0.21158456802368164-0.15383505821228027-0.147691011428833


-0.10439848899841309
-0.11252307891845703
-0.1019906997680664-0.16476702690124512
-0.12455368041992188
-0.10967707633972168
-0.16893482208251953
-0.17631983757019043

-0.1157839298248291
-0.1190953254699707
-0.1167304515838623-0.08667850494384766-0.12056589126586914

-0.33435821533203125

-0.11859989166259766
-0.1177210807800293
-0.12109017372131348
-0.11772513389587402-0.08891415596008301
-0.13385987281799316-0.13020682334899902

-0.06341195106506348

-0.08949828147888184
-0.12245035171508789-0.12570548057556152-0.1179356575012207

-0.09095406532287598

-0.09544253349304199
-0.15247249603271484
-0.06280040740966797
-0.1501176357269287
-0.13132452964782715
-0.10546183586120605
-0.34064245223999023
-0.33527588844299316-0.33808016777038574-0.10441732406616211


-0.06862592697143555
-0.36991381645202637
-0.09522318840026855
-0.31220269203186035
-0.09319162368774414-0.08638143539428711-0.

-0.15337252616882324-0.09160709381103516

-0.11958813667297363
-0.12498116493225098
-0.13434863090515137
-0.13896584510803223
-0.1343700885772705
-0.14918017387390137
-0.18401575088500977
-0.14568877220153809
-0.14380240440368652
-0.15790295600891113
-0.0933842658996582-0.08548903465270996-0.0796973705291748

-0.09167933464050293-0.3592524528503418

-0.18212485313415527

-0.11352372169494629-0.12246584892272949

-0.24296879768371582
-0.36434364318847656-0.11156463623046875-0.12135791778564453
-0.11575698852539062

-0.1211845874786377

-0.05066704750061035
-0.08990645408630371
-0.08535122871398926
-0.09763383865356445
-0.11072182655334473
-0.09553241729736328-0.09873414039611816-0.16292595863342285


-0.2508358955383301-0.2082536220550537-0.24900460243225098-0.418731689453125


-0.2149486541748047-0.22022581100463867


-0.2448103427886963
-0.15506482124328613
-0.2471637725830078-0.2818334102630615
-0.20212602615356445
-0.2077028751373291
-0.28970885276794434
-0.21282434463500977-0.21613

...

-0.25179600715637207
-0.11786961555480957-0.08393597602844238
-0.1257331371307373-0.11932373046875


-0.1586284637451172
-0.22979354858398438-0.11605691909790039
-0.24051141738891602
-0.0327296257019043
-0.23623991012573242-0.22732019424438477-0.04051375389099121

-0.01323246955871582-0.23804855346679688
-0.05489969253540039
-0.2333672046661377
-0.08611178398132324
-0.2191312313079834
-0.22734928131103516-0.10083675384521484-0.17906570434570312-0.022220134735107422
-0.2772989273071289-0.23774409294128418
-0.25481414794921875


-0.04257822036743164
-0.2550344467163086-0.23730063438415527
-0.0854344367980957
-0.24836421012878418-0.08599686622619629



-0.05219101905822754
-0.08659553527832031
-0.18148350715637207
-0.0986180305480957

-0.25884532928466797
-0.18869400024414062
-0.011171102523803711-0.2908768653869629-0.2474064826965332



-0.32184839248657227
-0.34807658195495605-0.21084356307983398
-0.14562320709228516
-0.034327030181884766


-0.30884218215942383

-0.11771726608276367
-0.

-0.08203864097595215-0.10203194618225098
-0.09981727600097656-0.10690140724182129
-0.07618117332458496

-0.2732198238372803
-0.08890628814697266

-0.3267250061035156
-0.06474447250366211-0.32482481002807617
-0.12065839767456055
-0.1262497901916504
-0.06858372688293457

-0.12302017211914062
-0.14155793190002441
-0.3509387969970703
-0.38114023208618164
-0.04017353057861328
-0.3244953155517578-0.3663921356201172
-0.07184481620788574

-0.006342172622680664-0.0453495979309082
-0.035132646560668945-0.03909754753112793-0.3603694438934326
-0.04599428176879883



-0.07260894775390625
-0.33376455307006836-0.027027368545532227

-0.3396763801574707-0.06182861328125

-0.04106926918029785-0.03525519371032715
-0.04723238945007324

-0.014427423477172852
-0.09207463264465332
-0.017681598663330078
-0.1574091911315918-0.3528885841369629
-0.05836057662963867

-0.13349580764770508-0.13614368438720703

-0.11871075630187988
-0.1743612289428711-0.14296603202819824

-0.02854752540588379
-0.06974148750305176
-0

-0.10733532905578613-0.1372535228729248

-0.11549949645996094

-0.054822444915771484
-0.07003474235534668
-0.23521924018859863
-0.09946966171264648-0.10248899459838867-0.10693526268005371
-0.1441960334777832


-0.08134675025939941
-0.08100676536560059
-0.1409320831298828
-0.3202486038208008
-0.10360121726989746
-0.11806130409240723
-0.10313105583190918
-0.03647279739379883-0.08739590644836426

-0.03659391403198242
-0.04498147964477539
-0.33180809020996094
-0.09846735000610352
-0.0970146656036377
-0.10147547721862793
-0.06088137626647949
-0.33751988410949707
-0.08361244201660156-0.050995826721191406

-0.07758450508117676
-0.3422117233276367-0.06987643241882324

-0.02723240852355957
-0.09490251541137695
-0.056824445724487305
-0.06167125701904297
-0.09498810768127441
-0.021810531616210938
-0.2519717216491699
-0.07740950584411621
-0.07962560653686523-0.11291170120239258

-0.1102604866027832
-0.06562066078186035
-0.07492470741271973
-0.09960055351257324
-0.07091379165649414-0.14719748497009

-0.25249481201171875
-0.023115873336791992
-0.02200484275817871
-0.03937840461730957-0.3624544143676758

-0.08527970314025879
-0.10312771797180176
-0.08210468292236328
-0.08705592155456543
-0.08539295196533203
-0.09753918647766113
-0.11150431632995605
-0.10990786552429199-0.09052157402038574-0.08677530288696289
-0.08119463920593262
-0.1200253963470459

-0.09384489059448242-0.14351940155029297
-0.10862946510314941


-0.11378860473632812-0.12250423431396484
-0.10247254371643066-0.11804819107055664


-0.11370515823364258
-0.003351926803588867
-0.07210826873779297
-0.09235811233520508
-0.07845616340637207
-0.17090415954589844
-0.18414092063903809-0.43137192726135254
-0.21078157424926758
-0.15966033935546875-0.12702226638793945-0.15828657150268555
-0.2199108600616455

-0.202286958694458


-0.07804560661315918-0.07609844207763672
-0.07149624824523926
-0.07059907913208008

-0.0747840404510498-0.07748150825500488-0.10687065124511719

-0.10383248329162598

-0.016573190689086914
-0.1032047271728

-0.009177923202514648
-0.09668445587158203-0.05250287055969238

-0.10414266586303711-0.11266803741455078

-0.018575668334960938
-0.008744001388549805
-0.0004508495330810547
-0.023941516876220703
-0.04030275344848633
-0.028927326202392578
-0.024945974349975586
-0.013909339904785156-0.012333393096923828
-0.0029032230377197266
-0.062377214431762695
-0.028476715087890625

-0.03988075256347656
-0.07385110855102539
-0.06175637245178223-0.0464475154876709
-0.07405924797058105

-0.09547948837280273
-0.05044674873352051
-0.08276867866516113-0.10001158714294434
-0.0518040657043457

-0.011074066162109375-0.017769575119018555
-0.020449399948120117
-0.01734781265258789
-0.018032312393188477
-0.03957676887512207

-0.058254241943359375
-0.09349584579467773
-0.25084400177001953
-0.42450857162475586-0.45162367820739746

-0.4588909149169922
-0.12410664558410645
-0.073272705078125
-0.21860599517822266
-0.12136983871459961
-0.11732053756713867-0.13013100624084473
-0.5667505264282227
-0.13858342170715332-0

In [ ]:
time.sleep(3 * 8640 // rate)

In [ ]:
Influx_Wide.run_all("2019-04-01T00:00:00", "2019-04-30T00:00:00", "d1_wide_slow_ingest")

In [ ]:
Influx_Wide.run_all("2019-05-01T01:00:00", "2019-05-02T00:00:00", "d1_wide_slow_ingest")

In [ ]:
Influx_Wide.run_all("2019-04-29T01:00:00", "2019-05-02T00:00:00", "d1_wide_slow_ingest")

In [37]:
stop_insertion = [True for i in range(n_threads)]


-3.5839366912841797
-3.481635332107544
-3.5834410190582275
-3.5778276920318604-3.5748517513275146
-3.5761146545410156-3.6526384353637695


-3.538099527359009-3.483187198638916
-3.4813930988311768

-3.609628915786743
-3.547264575958252-3.7040646076202393
-3.4758658409118652

-3.487185001373291
-3.526987075805664-3.4756362438201904

-3.5708184242248535
-3.517760992050171
-3.580259323120117
-3.533355951309204
-3.525413751602173
-3.5296573638916016
-3.5339837074279785
-3.6411967277526855
-3.775946855545044
-3.6975789070129395
-3.502187728881836
-3.640441417694092
-3.6946353912353516
-3.5653088092803955
-3.173433542251587
-3.3066024780273438
-3.2484655380249023
-3.207691192626953
-3.14949107170105
-3.166243553161621
-3.1242458820343018
-3.1246066093444824
-3.1243340969085693
-3.0826547145843506
-3.162862539291382
-3.4418177604675293-3.2804715633392334-3.0670924186706543


-3.1545190811157227-3.2004990577697754

-3.1594953536987305
-3.024543285369873
-2.949488639831543
-2.9086079597473145
-2

In [ ]:
results 

In [ ]:
runtimes = [[float(results[i][j].split('$')[0]) for j in range(len(results[i]))][:4] for i in range(5)]
variance = [[float(results[i][j].split('$')[2]) for j in range(len(results[i]))][:4] for i in range(5)]

In [ ]:
runtimes = list(map(list, zip(*runtimes)))
variance = list(map(list, zip(*variance)))


In [ ]:
runtimes

In [ ]:
import numpy as np
import matplotlib.pyplot as plt
X = np.arange(5)
labels = ['query'+str(1+i) for i in range(5)]
fig = plt.figure(figsize=(8, 6))
ax = fig.add_axes([0,0,1,1])
for i in range(4):
    ax.bar(X +0.15*i, runtimes[i], yerr = variance[i], width = 0.15)
ax.legend(['offline', 'online old', 'online new', 'online mixed', ])
ax.set_xticklabels(labels)
ax.set_xticks(np.arange(len(labels)))
ax.yaxis.grid(True)
plt.title('ClickHouse offline vs. online, rate: '+ str(rate) + ' x ' + str(n_threads))
plt.tight_layout()

# ax.bar(X+0.25, data[1], color = 'g', width = 0.25)
# ax.bar(X+0.5, data[2], color = 'r', width = 0.25)

In [38]:
from influxdb import InfluxDBClient
import time

start = time.time()
client = InfluxDBClient(host='diufrm118', port=8086, username='abdel', database='d1_wide')
result = client.query("""DELETE FROM "sensor" where time > '2019-04-30T00:00:00Z'""")
print(time.time() - start)

# result = client.query("select * into d1_wide_ingest.autogen.sensor FROM d1_wide.autogen.sensor")



0.2284679412841797
